In [1]:
# Import libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
% matplotlib inline
import os
import re
from nltk import word_tokenize, sent_tokenize
from nltk.corpus import stopwords
import string
from collections import defaultdict
from nltk.stem.porter import PorterStemmer
import pickle
from IPython.display import clear_output
from gensim import corpora, models
from gensim.models import Phrases, Word2Vec
from gensim.models.phrases import Phraser

In [2]:
# Read in and combine dfs of full dataset
funded_projects = pd.DataFrame()
for root, dirs, files in os.walk("data/completed_full_csv_parts/", topdown=True):
    for file in files:
        df = pd.read_csv(os.path.join(root, file))
        funded_projects = funded_projects.append(df)

/Users/maheshrao/anaconda3/envs/capstone/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (1,5,11,12,15,17,19,23,24,27) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/Users/maheshrao/anaconda3/envs/capstone/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (1,12,19,33) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/Users/maheshrao/anaconda3/envs/capstone/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (1,11,12,15,19,24) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/Users/maheshrao/anaconda3/envs/capstone/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (

In [3]:
# keep just R01s
funded_R01_projects = funded_projects[funded_projects.grant_num.str.contains("R01")]

In [4]:
years = funded_R01_projects.FY.astype(int).sort_values().unique().tolist()

In [5]:
# split by year, make list of dfs
dfs = list()
for year in years:
    df = funded_R01_projects[funded_R01_projects["FY"] == year]
    dfs.append(df)

In [6]:
strange_symbols = ["\xa0", "-\xad", "/"]

In [7]:
things_to_replace = ["unreadable",
                     "[unreadable]",
                     "DESCRIPTION",
                     "Application not provided", 
                     "Description Provided by Applicant",
                     "(Adapted from applicant's abstract)",
                     "(provided by applicant)",
                     "(Verbatim from applicants abstract)",
                     "Purpose",
                     "(Adapted from the Applicant's )",
                     " N A",
                     "(provided by investigator)",
                     "(From the Applicant's )",
                     "DESCRIPTION (provided by applicant)",
                     "ABSTRACT",
                     "Abstract",
                     "Project Summary/Abstract",
                     "PROJECT SUMMARY",
                     "Background:",
                     "Project Summary / Abstract",
                     "Project Summary",
                     "PROJECT SUMMARY/ABSTRACT",
                     "Summary/Abstract",
                     "||",
                     "Summary",
                     "PROJECT SUMMARY / ABSTRACT"]

In [8]:
punct = [p for p in string.punctuation]+["``", "''"]

In [9]:
stop_words = stopwords.words("english")

In [10]:
ps = PorterStemmer()

In [11]:
def average_token_length(doc):
    """calculate the average length of each token in a document"""
    
    #make list of lengths of each token
    lengths = list()
    for word in doc:
        l = len(word)
        lengths.append(l)
        
    #calculate mean
    if len(lengths) > 0:
        mean = np.mean(lengths)
    else:
        mean = 0
    
    return(mean)

In [12]:
def find_bad_abstracts(abs_list):
    
    abstracts = list()
    for abst in abs_list:
        abstract = word_tokenize(abst)
        abstracts.append(abstract)
        
    means = list()
    for a in abstracts:
        means.append(average_token_length(a))
        
    good_abstracts = []    
    for m, a in zip(means, abstracts):
        if m < 7:
            good_abstracts.append(a)
        
    return(good_abstracts)

In [13]:
def clean_abstract_text(df):
    
    
    abs_list = df.ABSTRACT_TEXT.tolist()
    
    for symb in strange_symbols:
        abs_list = [abstract.replace(symb, ' ') for abstract in abs_list]
        
    for phrase in things_to_replace:
        abs_list = [abstract.replace(phrase, '') for abstract in abs_list]
        
    abs_list = [re.sub(" +", " ", abstract) for abstract in abs_list]
    
    good_abstracts = find_bad_abstracts(abs_list)
    
    for ind, a in enumerate(good_abstracts):
        words = [word.lower() for word in a if word not in punct]
        words = [word for word in words if word not in stop_words]
        words = [word for word in words if not word.isdigit()]
        words = [ps.stem(word) for word in words]
        good_abstracts[ind] = words
        
    return(good_abstracts)

In [14]:
funding_summary = pd.read_html("data/RCDCFundingSummary071218.xls", header = 0)[0]

In [15]:
research_areas = funding_summary["Research/Disease Areas(Dollars in millions and rounded)"].tolist()

In [16]:
research_areas_cleaned = [re.sub(" \d+/", "", area) for area in research_areas]

In [24]:
def add_abstract_categories(df, col, new_col):
    
    """Search terms in selected col and return values that are in NIH list of research categories.
    Add list to new column. col and new_col should be strings"""
    
    column_list = df[col].tolist()
    
    terms_list = []
    for l in column_list:
        if type(l) != float:
            terms = l.split(";")
            terms_list.append(terms)
        else:
            terms_list.append([])
    
    categories = []
    for terms in terms_list:
        category = list(set(research_areas_cleaned) & set(terms))
        categories.append(category)
        
    df[new_col] = categories

In [25]:
cols = ["PROJECT_TERMS", "NIH_SPENDING_CATS"]
new_cols = ["topics_proj_terms", "topics_spending_cats"]

for c1, c2 in zip(cols, new_cols):
    add_abstract_categories(funded_R01_projects, c1, c2)

/Users/maheshrao/anaconda3/envs/capstone/lib/python3.6/site-packages/ipykernel_launcher.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [26]:
funded_R01_projects.columns

Index(['APPLICATION_ID', 'ARRA_FUNDED', 'AWARD_NOTICE_DATE', 'BUDGET_END',
       'BUDGET_START', 'CFDA_CODE', 'CORE_PROJECT_NUM', 'DIRECT_COST_AMT',
       'ED_INST_TYPE', 'FOA_NUMBER', 'FULL_PROJECT_NUM', 'FUNDING_ICs',
       'FUNDING_MECHANISM', 'FY', 'INDIRECT_COST_AMT', 'NIH_SPENDING_CATS',
       'ORG_CITY', 'ORG_DEPT', 'ORG_DISTRICT', 'ORG_DUNS', 'ORG_FIPS',
       'ORG_NAME', 'ORG_STATE', 'ORG_ZIPCODE', 'PHR', 'PI_IDS',
       'PROGRAM_OFFICER_NAME', 'PROJECT_END', 'PROJECT_START', 'PROJECT_TERMS',
       'PROJECT_TITLE', 'STUDY_SECTION', 'SUBPROJECT_ID', 'SUFFIX',
       'TOTAL_COST', 'TOTAL_COST_SUB_PROJECT', 'ABSTRACT_TEXT', 'grant_num',
       'topics_proj_terms', 'topics_spending_cats'],
      dtype='object')

In [27]:
topics_total = []
for r in funded_R01_projects.iterrows():
    row = r[1]
    total_topics = list(set(row.topics_proj_terms+row.topics_spending_cats))
    topics_total.append(total_topics)

In [28]:
funded_R01_projects["topics_total"] = topics_total

/Users/maheshrao/anaconda3/envs/capstone/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [29]:
funded_R01_projects.columns

Index(['APPLICATION_ID', 'ARRA_FUNDED', 'AWARD_NOTICE_DATE', 'BUDGET_END',
       'BUDGET_START', 'CFDA_CODE', 'CORE_PROJECT_NUM', 'DIRECT_COST_AMT',
       'ED_INST_TYPE', 'FOA_NUMBER', 'FULL_PROJECT_NUM', 'FUNDING_ICs',
       'FUNDING_MECHANISM', 'FY', 'INDIRECT_COST_AMT', 'NIH_SPENDING_CATS',
       'ORG_CITY', 'ORG_DEPT', 'ORG_DISTRICT', 'ORG_DUNS', 'ORG_FIPS',
       'ORG_NAME', 'ORG_STATE', 'ORG_ZIPCODE', 'PHR', 'PI_IDS',
       'PROGRAM_OFFICER_NAME', 'PROJECT_END', 'PROJECT_START', 'PROJECT_TERMS',
       'PROJECT_TITLE', 'STUDY_SECTION', 'SUBPROJECT_ID', 'SUFFIX',
       'TOTAL_COST', 'TOTAL_COST_SUB_PROJECT', 'ABSTRACT_TEXT', 'grant_num',
       'topics_proj_terms', 'topics_spending_cats', 'topics_total'],
      dtype='object')

In [48]:
abstract_topic = funded_R01_projects[["FY", "ABSTRACT_TEXT", "topics_total"]]

In [31]:
inds_per_cat = []
for c in research_areas_cleaned:
    inds = []
    for ind, l in enumerate(abstract_topic.topics_total):
        if c in l:
            inds.append(ind)
    inds_per_cat.append(inds)

In [33]:
cat_dfs_list = [abstract_topic.iloc[cat] for cat in inds_per_cat]

In [42]:
topics_with_abstracts = []
for cat, df in zip(research_areas_cleaned, cat_dfs_list):
    if len(df) > 0:
        topics_with_abstracts.append((cat, df))
        print(len(df))

1539
1031
518
52
24157
854
41
647
4527
251
302
2280
1170
230
87
2327
2428
2896
190
4750
616
1834
7148
102
12200
45
24764
5072
21854
39132
596
1839
22739
4701
96
137
29960
2
51
13693
256
9
314
188
191
286
28
2218
513
31
239
37537
1232
764
2025
333
2687
106
236
301
1059
1537
3034
2760
5363
355
22
8585
34
119
344
142
170
250
7
40
6537
181
160
60
1825
1423
35
209
46
98
9
11
276
77
1074
16
1070
42485
10
46
1
2
2640
5531
1885
4406
920
8
186
437
3888
82
118
7
59
169
5816
429
96
32
3660
3901
200
14066
925
497
813
176
1052
420
101
2409
114
3159
74
532
3024
8320
793
717
176
1009
431
979
780
45
62
11198
504
26
2818
61
1263
377
62
130
1291
16
1433
399
8413
95
31303
6920
5197
1013
1750
139
53
1479
180
443
20
1797
81
202
703
720
11154
362
927
74
1877
71
7
1057
208
2
2638
69
18999
1362
230
75
1734
4283
2363
147
1
944
449
2499
128
59
600
1123
165
1308
85
1564
74
535
114
5037
301
693
18
13
5
1031
3399
188
160
36
1972
6798
62
83
447
37
133
94
1942
76
61
184
3918
849
93
153
143
2240
30
82
3250
1568
208
9

In [45]:
cleaned_abstracts = []
l = len(topics_with_abstracts)
for ind, cat in enumerate(topics_with_abstracts):
    cleaned_abstracts.append(clean_abstract_text(cat[1]))
    clear_output()
    print("finished {} out of {}".format(ind+1, l))

finished 27 out of 249


KeyboardInterrupt: 

In [47]:
cleaned_abstracts[0]

[['grant',
  'focus',
  'alzheim',
  "'s",
  'diseas',
  'ad',
  'frequent',
  'neurodegen',
  'condit',
  'question',
  'elev',
  'amyloid-beta',
  'a-beta',
  'level',
  'brain',
  'contribut',
  'pathogenesi',
  'recent',
  'discov',
  'explor',
  'novel',
  'environ',
  'caus',
  'put',
  'dna',
  'doubl',
  'strand',
  'break',
  'dsb',
  'neuron',
  'wildtyp',
  'wt',
  'mice',
  'dsb',
  'abund',
  'memori',
  'center',
  'repair',
  'within',
  'hour',
  'transgen',
  'mice',
  'neuron',
  'express',
  'famili',
  'ad-mut',
  'form',
  'human',
  'amyloid',
  'precursor',
  'protein',
  'happfad',
  'mice',
  'simul',
  'sever',
  'aspect',
  'ad',
  'increas',
  'neuron',
  'dsb',
  'baselin',
  'sever',
  'prolong',
  'dsb',
  'explor',
  'treatment',
  'anti-epilept',
  'drug',
  'levetiracetam',
  'suppress',
  'aberr',
  'network',
  'activ',
  'normal',
  'level',
  'dsb',
  'improv',
  'synapt',
  'function',
  'well',
  'learn',
  'memori',
  'happfad',
  'mice',
  'pri

In [59]:
abstract_topic_2008 = abstract_topic[abstract_topic.FY == 2008]

In [52]:
[cat for cat in research_areas_cleaned if "eurosci" in cat]

['Neurosciences']

In [61]:
neurosciences = []
not_neurosciences = []
for ind, l in enumerate(abstract_topic_2008.topics_total):
    if "Neurosciences" in l:
        neurosciences.append(ind)
    else:
        not_neurosciences.append(ind)

In [64]:
neuro_2008_df = abstract_topic_2008.iloc[neurosciences]
not_neuro_2008_df = abstract_topic_2008.iloc[not_neurosciences]